In [1]:
# !pip install sentence-transformers==2.0.0

In [2]:
import pandas as pd
from tqdm import tqdm
from sentence_transformers import SentenceTransformer

model = SentenceTransformer('all-mpnet-base-v2') #all-MiniLM-L6-v2 #all-mpnet-base-v2

c:\Users\ardit\AppData\Local\Programs\Python\Python39\lib\site-packages\torch\onnx\_internal\_beartype.py:30: UserWarning: module 'beartype.roar' has no attribute 'BeartypeDecorHintPep585DeprecationWarning'
  warnings.warn(f"{e}")


In [ ]:
df = pd.read_parquet('df_encoded.parquet')
df

In [17]:
from sklearn.neighbors import NearestNeighbors
import numpy as np
import pandas as pd

from sentence_transformers import SentenceTransformer

model = SentenceTransformer('all-mpnet-base-v2') #all-MiniLM-L6-v2 #all-mpnet-base-v2

#prepare model
# nbrs = NearestNeighbors(n_neighbors=8, algorithm='ball_tree').fit(df['text_vector_'].values.tolist())

In [19]:
def filter_df(df, column_name, filter_type, filter_value):
    if filter_type == '==':
        df_filtered = df[df[column_name]==filter_value]
    elif filter_type == '<=':
        df_filtered = df[df[column_name]<=filter_value]
    return df_filtered

def search(df, query):
    product = model.encode(query).tolist()
    # product = df.iloc[0]['text_vector_'] #use one of the products as sample

    nbrs = NearestNeighbors(n_neighbors=8, algorithm='ball_tree').fit(df['text_vector_'].values.tolist())
    distances, indices = nbrs.kneighbors([product]) #input the vector of the reference object

    #print out the description of every recommended product
    df_search = df.iloc[list(indices)[0]].drop(['skills', 'text_vector_'], axis=1).sort_values('avgFeedbackScore', ascending=False)

    return df_search[['shortName', 'location', 'title', 'hourlyRate', 'avgFeedbackScore', 'description']]

# search('I want to hire a person who does both backend and')

df_location = filter_df(df, 'location', '==', 'New York')
df_price = filter_df(df_location, 'hourlyRate', '<=', 80)
search(df_price, 'I want to hire a person who does both backend and')

shortName  location  \
3761     Steven F.  New York   
835   Jacquelyn N.  New York   
2787       Mark H.  New York   
3402   Carleton C.  New York   
1156      Andee F.  New York   
1556      Laura O.  New York   
1002     Nicole H.  New York   
1626       Drew L.  New York   

                                                  title  hourlyRate  \
3761          Database Manger / Graphics / Social Media        35.0   
835                            Admin support specialist        12.0   
2787  WordPress Specialist - Development, Administra...        60.0   
3402  Expert freelancer with skills in Divi theme, C...        25.0   
1156                             Experienced Freelancer        15.0   
1556  Admin Expert with experience in Microsoft Suit...        30.0   
1002  Experienced admin support and customer support...        30.0   
1626                            Front End Web Developer        50.0   

      avgFeedbackScore                                        description  
3761          4.939631  A highly skilled problem solver​ with over 10 ...  
835           4.920992  I am a Kansas City based Virtual Assistant. I ...  
2787          4.751762  Top Rated Plus | Specialize in WordPress | Inv...  
3402          4.692159  For over 30 years, I have developed a wide ran...  
1156          4.645855  I have 8+ years of successfully providing admi...  
1556          4.620818  I have been passionate about my personal budge...  
1002          4.129972  I'm an experienced jack of all trades.  I have...  
1626          0.000000  Worked for agency with big name clients doing ...

In [ ]:
import gradio as gr
import os

#the first module becomes text1, the second module file1
def greet(price, location, query):
    # df1 = 
    df_location = filter_df(df, 'location', '==', location)
    df_price = filter_df(df_location, 'hourlyRate', '<=', price)
    df_search = search(df_price, query)
    return df_search

In [28]:
with gr.Blocks(theme=gr.themes.Soft(primary_hue='amber', secondary_hue='gray', neutral_hue='amber')) as demo:
    gr.Markdown(
    """
    # Freelancer Upwork Search
    """
    )
    input1 = gr.Slider(20, 120, value=90, step_size=5, label="Max Hourly Rate")
    input2 = gr.Radio(['New York', 'Chicago', 'Washington'], multiselect=False, label='State', value='New York')
    input3 = gr.Textbox(label='Query', value='I want to develop a mobile app')

    btn = gr.Button(value="Search for Product")
    output = gr.Dataframe()
    # btn.click(greet, inputs='text', outputs=['dataframe'])
    btn.click(greet, [input1, input2, input3], [output])
demo.launch(share=False)

c:\Users\ardit\AppData\Local\Programs\Python\Python39\lib\site-packages\gradio\deprecation.py:43: UserWarning: You have unused kwarg parameters in Slider, please remove them: {'step_size': 5}
  warnings.warn(
c:\Users\ardit\AppData\Local\Programs\Python\Python39\lib\site-packages\gradio\deprecation.py:43: UserWarning: You have unused kwarg parameters in Radio, please remove them: {'multiselect': False}
  warnings.warn(


Running on local URL:  http://127.0.0.1:7906

To create a public link, set `share=True` in `launch()`.


In [ ]:
# iface = gr.Interface(
#     fn=greet,
#     inputs=[
#         gr.Slider(20, 120, value=20, step_size=5, label="Max Hourly Rate"),
#         gr.Radio(
#             ['New York', 'Chicago', 'Washington'], multiselect=False, label='State', value='New York'
#         ),
#         gr.Textbox(label='Input', value='I want to develop a mobile app')
#     ],
#     outputs=["dataframe"])
# iface.launch(share=False)